# FARGOpy
## Wrapping FRAGO3D

## Tutorial: using `plotly`

<a target="_blank" href="https://colab.research.google.com/github/seap-udea/fargopy/blob/main/examples/fargopy-tutorial-plotly.ipynb">
  <img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/>
</a>

### What's in this notebook

In this notebook we illustrate **how to use `plotly` capabilities to plot simulation results** in `FARGOpy`.

### Before starting

If you are in `Google Colab`, install the latest version of the package:

In [2]:
# @title Install fargopy
import sys
if 'google.colab' in sys.modules:
    !sudo pip install -Uq fargopy plotly

For this tutorial you will need the following external modules and tools:

In [3]:
import fargopy as fp
import numpy as np 
import matplotlib.pyplot as plt
import pandas as pd
import plotly.graph_objects as go

%load_ext autoreload
%autoreload 2

Running FARGOpy version 0.3.6


### Let's `FARGOpy`

Let's download a precomputed simulation:

In [6]:
fp.Simulation.download_precomputed('p3disoj')

Downloading...
From: https://docs.google.com/uc?export=download&id=1Xzgk9qatZPNX8mLmB58R9NIi_YQUrHz9
To: /tmp/p3disoj.tgz
100%|██████████| 84.2M/84.2M [00:02<00:00, 35.4MB/s]


Uncompressing p3disoj.tgz into /tmp/p3disoj
Done.


Load the simulation and read the density field:

In [59]:
# Connect to the simulation results
sim = fp.Simulation(output_dir='/tmp/p3disoj')

# Get fields and slice them
snap = 10
gasdens = sim.load_field('gasdens',type='scalar',snapshot=snap)

Your simulation is now connected with '/home/jzuluaga/fargo3d/'
Now you are connected with output directory '/tmp/p3disoj'
Found a variables.par file in '/tmp/p3disoj', loading properties
Loading variables
85 variables loaded
Simulation in 3 dimensions
Loading domain in spherical coordinates:
	Variable phi: 128 [[0, -3.117048960983623], [-1, 3.117048960983623]]
	Variable r: 64 [[0, 0.5078125], [-1, 1.4921875]]
	Variable theta: 32 [[0, 1.4231400767948967], [-1, 1.5684525767948965]]
Number of snapshots in output directory: 11
Configuration variables and domains load into the object. See e.g. <sim>.vars


We want to create a 3 dimensional representation of the field. First let's slice the filed on a plane of constant $\varphi$:

In [115]:
slice = "phi=0"
gasdens_slice,mesh = gasdens.meshslice(slice=slice)

Now create a 3D scatter plot of the field:

In [116]:
xmin = mesh.x.min()
xmax = mesh.x.max()
range = xmax - xmin
ymin = mesh.y.min() - range/2
ymax = mesh.y.max() + range/2
zmin = mesh.z.min()
zmax = mesh.z.max()


In [117]:
from IPython.display import display, HTML
fig = go.Figure()

fig.add_trace(
    go.Scatter3d(
        x=mesh.x.flatten(),
        y=mesh.y.flatten(),
        z=mesh.z.flatten(),
        mode='markers',
        marker=dict(
            size=4,
            color=np.log10(gasdens_slice).flatten(),
            colorscale='thermal',
            opacity=0.5
        )
    )
)

fig.update_layout(
    autosize=False,
    width=600,
    height=600,
    scene=dict(
        aspectmode='cube',
        xaxis=dict(range=[xmin, xmax]),
        yaxis=dict(range=[ymin, ymax]),
        zaxis=dict(range=[zmin, zmax]),
        #xaxis_visible=False,
        #yaxis_visible=False,
        #zaxis_visible=False,
    ),
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
)

# Show the plot
fig.show()

Let's do it at different angles:

In [111]:
from IPython.display import display, HTML
fig = go.Figure()

dphi = 15
for phi in np.arange(0,90+dphi,dphi):

    slice = f"phi={phi} deg"
    gasdens_slice,mesh = gasdens.meshslice(slice=slice)

    fig.add_trace(
        go.Scatter3d(
            x=mesh.x.flatten(),
            y=mesh.y.flatten(),
            z=mesh.z.flatten(),
            mode='markers',
            name='phi = '+str(phi)+' deg',
            marker=dict(
                size=5,
                color=np.log10(gasdens_slice).flatten(),
                colorscale='thermal',
                opacity=1
            )
        )
    )

fig.update_layout(
    autosize=False,
    width=600,
    height=600,
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
    scene=dict(aspectmode='cube'),
    scene_camera = dict(
        up=dict(x=0,y=0,z=1),
        center=dict(x=0,y=0,z=0),
        eye=dict(x=0,y=-2,z=0.5)
    ),
)

# Show the plot
fig.show()

You can represent density as a surface. First slicing it:

In [118]:
slice = "itheta=0"
gasdens_plane,mesh = gasdens.meshslice(slice=slice)

And then plotting the surface:

In [124]:
fig = go.Figure()

fig.add_trace(
    go.Surface(
        x=mesh.x,
        y=mesh.y,
        z=np.log10(gasdens_plane),
        contours=dict(
            z=dict(
                show=True,
                usecolormap=True,
                highlightcolor="limegreen",
                project=dict(z=True)
            )
        ),
        colorscale='thermal',
        opacity=1,
        showscale=False
    )
)

fig.update_layout(
    autosize=False,
    width=600,
    height=600,
    scene=dict(
        aspectmode='cube',
        xaxis=dict(title='X'),
        yaxis=dict(title='Y'),
        zaxis=dict(title='Z'),
    ),
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
)

fig.show()
